#  APIs for Financial Data

---

<br>
For both parts of this project, I will use Python to interact with the Alpha Vantage API and export data from different endpoints to answer two research questions.

# Part 1: GDP and Consumer Sentiment during the pandemic

I have been tasked with analysing how various economic indicators have behaved during the last few years. <br>

I have identified a free source of this data: Alpha Vantage (https://www.alphavantage.co) and will extract relevant data about these indicators and write a short report about my findings.

In [6]:
import pandas as pd
import json
import requests
import plotly.graph_objects as go
from plotly.subplots import make_subplots

**1. Identify the correct API endpoint to retrieve historical data on GDP**

In [ ]:
base_url = 'https://www.alphavantage.co/query'

In [8]:
# The API key is stored separately on a config file for security reasons
with open("config.json") as f:
    config = json.load(f)
    API_KEY = config["API_KEY"]

Defined a variable `base_url` that will form the base portion of the Alpha Vantage URL endpoint and another variable `API_KEY` as the Alpha Vantage API key.

**2. Use the `requests` library to make an API call and retrieve historical GDP data at *the highest level of granularity***

In [9]:
# Retrieve API for GDP quarterly data of the United States
GDP_response = requests.get(f'{base_url}?function=REAL_GDP&interval=quarterly&apikey={API_KEY}')
GDP_data = GDP_response.json()

In [ ]:
# Retrieve API using search function to identify equity names and types
# search_response = requests.get(f'{base_url}?function=SYMBOL_SEARCH&keywords=VXX&apikey={API_KEY}')
# search_data = search_response.json()
# search_data

**3. Convert the data in the JSON retrieved from Alpha Vantage to a Pandas dataframe and export to a csv.**

In [ ]:
# Convert json to dataframe, rename columns, and export as csv file
GDP_df = pd.DataFrame(GDP_data['data'])
GDP_df = GDP_df.rename(columns = {'date' : 'Date', 'value' : 'Value'})
GDP_df.to_csv('./Datasets/GDP_quarterly data.csv', index = False)

**4. Next, identify the endpoint for finding daily stock price values, query the VXX ticker and export it to a csv.**

In [ ]:
# Retrieve API for VXX mutual fund time series daily adjusted data for 20+ years of historical data
VXX_response = requests.get(f'{base_url}?function=TIME_SERIES_DAILY&symbol=VXX&outputsize=full&apikey={API_KEY}')
VXX_data = VXX_response.json()

In [ ]:
# Convert json to dataframe, tranpose rows and columns, rename columns, and export as csv file
VXX_df = pd.DataFrame(VXX_data['Time Series (Daily)'])
VXX_df = VXX_df.T.reset_index()
VXX_df = VXX_df.rename(columns = {'index' : 'Date', '1. open' : 'Open', '2. high' : 'High', '3. low' : 'Low', '4. close' : 'Close', '5. volume' : 'Volume'})
VXX_df.to_csv('./Datasets/VXX_daily data.csv', index = False)

VXX is a mutual fund that represents the fear and volatility in the market. When VXX is high, fear controls the market, and when VXX is low, people have more confidence in the market.

**5. Identify the endpoint for the VTI ticker and export it to a csv.**

In [ ]:
# Retrieve API for VTI mutual fund time series daily adjusted data for 20+ years of historical data
VTI_response = requests.get(f'{base_url}?function=TIME_SERIES_DAILY&symbol=VTI&outputsize=full&apikey={API_KEY}')
VTI_data = VTI_response.json()

In [ ]:
# Convert json to dataframe, tranpose rows and columns, rename columns, and export as csv file
VTI_df = pd.DataFrame(VTI_data['Time Series (Daily)'])
VTI_df = VTI_df.T.reset_index()
VTI_df = VTI_df.rename(columns = {'index' : 'Date', '1. open' : 'Open', '2. high' : 'High', '3. low' : 'Low', '4. close' : 'Close', '5. volume' : 'Volume'})
VTI_df.to_csv('./Datasets/VTI_daily data.csv', index = False)

VTI is a mutual fund that consists of _every_ US stock and can be considered an indicator for the overall market.

In [ ]:
# Read saved csv files
GDP_df = pd.read_csv('./Datasets/GDP_quarterly data.csv')
VTI_df = pd.read_csv('./Datasets/VTI_daily data.csv')
VXX_df = pd.read_csv('./Datasets/VXX_daily data.csv')

In [ ]:
# Copy data into new dataframes for cleaning 
GDP_cleaned_df = GDP_df.copy()
VXX_cleaned_df = VXX_df.copy()
VTI_cleaned_df = VTI_df.copy()

**6. Clean the data by checking it for nulls and duplicate values.**

In [ ]:
print(GDP_cleaned_df.isnull().sum())
print(VXX_cleaned_df.isnull().sum())
print(VTI_cleaned_df.isnull().sum())
print(GDP_cleaned_df.duplicated().any())
print(VXX_cleaned_df.duplicated().any())
print(VTI_cleaned_df.duplicated().any())

Date     0
Value    0
dtype: int64
Date      0
Open      0
High      0
Low       0
Close     0
Volume    0
dtype: int64
Date      0
Open      0
High      0
Low       0
Close     0
Volume    0
dtype: int64
False
False
False


**7. Convert date from object to datetime datatype and share price and GDP information from object to float datatype.**

In [ ]:
GDP_cleaned_df['Date'] = pd.to_datetime(GDP_cleaned_df['Date'])
VXX_cleaned_df['Date'] = pd.to_datetime(VXX_cleaned_df['Date'])
VTI_cleaned_df['Date'] = pd.to_datetime(VTI_cleaned_df['Date'])

GDP_cleaned_df['Value'] = GDP_df['Value'].astype(float).round(2)
VXX_cleaned_df[['Open', 'High', 'Low', 'Close', 'Volume']] = VXX_cleaned_df[['Open', 'High', 'Low', 'Close', 'Volume']].astype(float).round(2)
VTI_cleaned_df[['Open', 'High', 'Low', 'Close', 'Volume']] = VTI_cleaned_df[['Open', 'High', 'Low', 'Close', 'Volume']].astype(float).round(2)

print(GDP_cleaned_df.info())
print(VXX_cleaned_df.info())
print(VTI_cleaned_df.info())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 93 entries, 0 to 92
Data columns (total 2 columns):
 #   Column  Non-Null Count  Dtype         
---  ------  --------------  -----         
 0   Date    93 non-null     datetime64[ns]
 1   Value   93 non-null     float64       
dtypes: datetime64[ns](1), float64(1)
memory usage: 1.6 KB
None
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4130 entries, 0 to 4129
Data columns (total 6 columns):
 #   Column  Non-Null Count  Dtype         
---  ------  --------------  -----         
 0   Date    4130 non-null   datetime64[ns]
 1   Open    4130 non-null   float64       
 2   High    4130 non-null   float64       
 3   Low     4130 non-null   float64       
 4   Close   4130 non-null   float64       
 5   Volume  4130 non-null   float64       
dtypes: datetime64[ns](1), float64(5)
memory usage: 193.7 KB
None
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6057 entries, 0 to 6056
Data columns (total 6 columns):
 #   Column  Non-Null Count 

**8. Calculate new columns for daily return, 5-day moving average, and 5-day rolling volatility.**

In [ ]:
VTI_cleaned_df['Daily Return (%)'] = (VTI_cleaned_df['Close'].pct_change() * 100).round(2)
VTI_cleaned_df['5-Day Moving Average'] = VTI_cleaned_df['Close'].rolling(window = 5).mean().round(2)
VTI_cleaned_df['5-Day Rolling Volatility'] = VTI_cleaned_df['Daily Return (%)'].rolling(window = 5).std().round(2)
VXX_cleaned_df['Daily Return (%)'] = (VXX_cleaned_df['Close'].pct_change() * 100).round(2)
VXX_cleaned_df['5-Day Moving Average'] = VXX_cleaned_df['Close'].rolling(window = 5).mean().round(2)
VXX_cleaned_df['5-Day Rolling Volatility'] = VXX_cleaned_df['Daily Return (%)'].rolling(window = 5).std().round(2)

In [ ]:
# After cleaning and adding new columns, export cleaned data as new csv files
GDP_cleaned_df.to_csv('./Datasets/GDP_cleaned_daily data.csv', index = False)
VTI_cleaned_df.to_csv('./Datasets/VTI_cleaned_daily data.csv', index = False)
VXX_cleaned_df.to_csv('./Datasets/VXX_cleaned_daily data.csv', index = False)

**9. Create plots of the various economic indicators for exploratory data analysis.**

In [ ]:
# Create a subplot of GDP line plot, VXX, and VTI candlestick plots from Jan 2024 to Jan 2025
fig = make_subplots(rows = 3, cols = 1, shared_xaxes = True, subplot_titles=('GDP', 'VTI ETF', 'VXX ETN'), vertical_spacing = 0.05, y_title = "USD")

fig.add_trace(go.Scatter(x = GDP_cleaned_df['Date'], y = GDP_cleaned_df['Value'], name = 'GDP', mode = 'lines+markers', marker = dict(size = 8), line = dict(color = 'blue', width = 2), 
                         showlegend = False), row = 1, col = 1)

fig.add_trace(go.Candlestick(x = VTI_cleaned_df['Date'], open = VTI_cleaned_df['Open'], high = VTI_cleaned_df['High'], low = VTI_cleaned_df['Low'], close = VTI_cleaned_df['Close'], 
                             name = 'Candlesticks', showlegend = True), row = 2, col = 1)
fig.add_trace(go.Scatter(x = VTI_cleaned_df['Date'], y = VTI_cleaned_df['5-Day Moving Average'], line = dict(color = 'black', width=1), name = "5-Day Moving Average", showlegend = True), 
                        row = 2, col = 1)

fig.add_trace(go.Candlestick(x = VXX_cleaned_df['Date'], open = VXX_cleaned_df['Open'], high = VXX_cleaned_df['High'], low = VXX_cleaned_df['Low'], close = VXX_cleaned_df['Close'], 
                             name = 'VXX', showlegend = False), row = 3, col = 1)
fig.add_trace(go.Scatter(x = VXX_cleaned_df['Date'], y = VXX_cleaned_df['5-Day Moving Average'], line = dict(color = 'black', width=1), name = "5-Day Moving Average", showlegend = False), 
                        row = 3, col = 1)

fig.update_layout(title = {'x' : 0.5, 'y' : 1, 'xanchor' : 'center'}, margin = dict(l = 65, r = 40, t = 40, b = 30), hovermode="x", width = 750, height = 750, 
                  legend=dict(x = 0.05, y = 0.6, xanchor = 'left', yanchor = 'top', bgcolor = 'rgba(255, 255, 255, 0.5)'))

fig.update_yaxes(range=[5550, 6050], row = 1, col = 1)
fig.update_yaxes(range=[220, 310], row = 2, col = 1)
fig.update_yaxes(range=[0, 100], row = 3, col = 1)

fig.update_xaxes(range=['2023-12-25', '2025-01-05'], row = 1, col = 1)
fig.update_xaxes(range=['2023-12-25', '2025-01-05'], row = 2, col = 1)
fig.update_xaxes(range=['2023-12-25', '2025-01-05'], row = 3, col = 1)
fig.update_xaxes(rangeslider_visible=False)

fig.show()

In [ ]:
# Create a subplot of GDP line plot, VXX, and VTI candlestick plots from Jul 2015 to Jul 2025
fig2 = make_subplots(rows = 3, cols = 1, shared_xaxes = True, subplot_titles=('GDP', 'VTI ETF', 'VXX ETN'), vertical_spacing = 0.05, y_title = "USD")

fig2.add_trace(go.Scatter(x = GDP_cleaned_df['Date'], y = GDP_cleaned_df['Value'], name = 'GDP', mode = 'lines+markers', line = dict(color = 'blue', width = 2), showlegend = False), row = 1, col = 1)

fig2.add_trace(go.Candlestick(x = VTI_cleaned_df['Date'], open = VTI_cleaned_df['Open'], high = VTI_cleaned_df['High'], low = VTI_cleaned_df['Low'], close = VTI_cleaned_df['Close'], 
                              name = 'Candlesticks', showlegend = True), row = 2, col = 1)
fig2.add_trace(go.Scatter(x = VTI_cleaned_df['Date'], y = VTI_cleaned_df['5-Day Rolling Volatility'], line = dict(color = 'black', width=1), name = "5-Day Rolling Volatility", showlegend = True), 
                          row = 2, col = 1)

fig2.add_trace(go.Candlestick(x = VXX_cleaned_df['Date'], open = VXX_cleaned_df['Open'], high = VXX_cleaned_df['High'], low = VXX_cleaned_df['Low'], close = VXX_cleaned_df['Close'], 
                              name = 'VXX', showlegend = False), row = 3, col = 1)
fig2.add_trace(go.Scatter(x = VXX_cleaned_df['Date'], y = VXX_cleaned_df['5-Day Rolling Volatility'], line = dict(color = 'black', width=1), name = "5-Day Rolling Volatility", showlegend = False), 
               row = 3, col = 1)

fig2.update_layout(title = {'x' : 0.5, 'y' : 1, 'xanchor' : 'center'}, margin = dict(l = 65, r = 40, t = 40, b = 30), hovermode="x", width = 750, height = 750, 
                  legend=dict(x = 0.05, y = 0.61, xanchor = 'left', yanchor = 'top', bgcolor = 'rgba(255, 255, 255, 0.5)'))

fig2.update_yaxes(range=[4400, 6200], row = 1, col = 1)
fig2.update_yaxes(range=[-50, 350], row = 2, col = 1)
fig2.update_yaxes(range=[-10, 100], row = 3, col = 1)

fig2.update_xaxes(range=['2015-07-01', '2025-07-02'], row = 1, col = 1)
fig2.update_xaxes(range=['2015-07-01', '2025-07-02'], row = 2, col = 1)
fig2.update_xaxes(range=['2015-07-01', '2025-07-02'], row = 3, col = 1)
fig2.update_xaxes(rangeslider_visible=False)

fig2.show()

# Part 2: Cryptocurrencies

Stakeholders are becoming aware of the rise in cryptocurrencies, and would like to understand the recent growth of this market. <br>

My task is to use the Alpha Vantage API to extract historical data on cryptocurrency market performance and write a short report about my findings.

**1. Find the correct API endpoints to retrieve historical data on Bitcoin, Ethereum, XRP, Dogecoin, and Solana over time.**

In [ ]:
# Retrieve API for top 5 cryptocurrencies based on current market capitalization for 1 year of historical data, 
# Exclusions: USDT and UDSC cryptocurrencies which are pegged to the USD and lack price volatility. BNB and Tron cryptocurrency data are not available on Alpha Vantage API 
bitcoin_response = requests.get(f'{base_url}?function=DIGITAL_CURRENCY_DAILY&symbol=BTC&market=USD&apikey={API_KEY}')
bitcoin_data = bitcoin_response.json()

ethereum_response = requests.get(f'{base_url}?function=DIGITAL_CURRENCY_DAILY&symbol=ETH&market=USD&apikey={API_KEY}')
ethereum_data = ethereum_response.json()

xrp_response = requests.get(f'{base_url}?function=DIGITAL_CURRENCY_DAILY&symbol=XRP&market=USD&apikey={API_KEY}')
xrp_data = xrp_response.json()

dogecoin_response = requests.get(f'{base_url}?function=DIGITAL_CURRENCY_DAILY&symbol=DOGE&market=USD&apikey={API_KEY}')
dogecoin_data = dogecoin_response.json()

solana_response = requests.get(f'{base_url}?function=DIGITAL_CURRENCY_DAILY&symbol=SOL&market=USD&apikey={API_KEY}')
solana_data = solana_response.json()

**2. Identify the key which holds the data itself and export it as a csv.**

In [ ]:
# Convert json to dataframe and export as csv file
bitcoin_df = pd.DataFrame(bitcoin_data['Time Series (Digital Currency Daily)'])
bitcoin_df = bitcoin_df.T.reset_index()
bitcoin_df = bitcoin_df.rename(columns = {'index' : 'Date', '1. open' : 'Open', '2. high' : 'High', '3. low' : 'Low', '4. close' : 'Close', '5. volume' : 'Volume'})
bitcoin_df.to_csv('./Datasets/Bitcoin_daily data.csv', index = False)

ethereum_df = pd.DataFrame(ethereum_data['Time Series (Digital Currency Daily)'])
ethereum_df = ethereum_df.T.reset_index()
ethereum_df = ethereum_df.rename(columns = {'index' : 'Date', '1. open' : 'Open', '2. high' : 'High', '3. low' : 'Low', '4. close' : 'Close', '5. volume' : 'Volume'})
ethereum_df.to_csv('./Datasets/Ethereum_daily data.csv', index = False)

xrp_df = pd.DataFrame(xrp_data['Time Series (Digital Currency Daily)'])
xrp_df = xrp_df.T.reset_index()
xrp_df = xrp_df.rename(columns = {'index' : 'Date', '1. open' : 'Open', '2. high' : 'High', '3. low' : 'Low', '4. close' : 'Close', '5. volume' : 'Volume'})
xrp_df.to_csv('./Datasets/XRP_daily data.csv', index = False)

dogecoin_df = pd.DataFrame(dogecoin_data['Time Series (Digital Currency Daily)'])
dogecoin_df = dogecoin_df.T.reset_index()
dogecoin_df = dogecoin_df.rename(columns = {'index' : 'Date', '1. open' : 'Open', '2. high' : 'High', '3. low' : 'Low', '4. close' : 'Close', '5. volume' : 'Volume'})
dogecoin_df.to_csv('./Datasets/Dogecoin_daily data.csv', index = False)

solana_df = pd.DataFrame(solana_data['Time Series (Digital Currency Daily)'])
solana_df = solana_df.T.reset_index()
solana_df = solana_df.rename(columns = {'index' : 'Date', '1. open' : 'Open', '2. high' : 'High', '3. low' : 'Low', '4. close' : 'Close', '5. volume' : 'Volume'})
solana_df.to_csv('./Datasets/Solana_daily data.csv', index = False)

In [11]:
# Read saved csv files
bitcoin_df = pd.read_csv('./Datasets/Bitcoin_daily data.csv')
ethereum_df = pd.read_csv('./Datasets/Ethereum_daily data.csv')
xrp_df = pd.read_csv('./Datasets/XRP_daily data.csv')
dogecoin_df = pd.read_csv('./Datasets/Dogecoin_daily data.csv')
solana_df = pd.read_csv('./Datasets/Solana_daily data.csv')

In [12]:
# Copy data into new dataframes for cleaning 
bitcoin_cleaned_df = bitcoin_df.copy()
ethereum_cleaned_df = ethereum_df.copy()
xrp_cleaned_df = xrp_df.copy()
dogecoin_cleaned_df = dogecoin_df.copy()
solana_cleaned_df = solana_df.copy()

**3. Clean the data by checking it for nulls and duplicate values.**

In [ ]:
print(bitcoin_cleaned_df.isnull().sum())
print(bitcoin_cleaned_df.duplicated().any())

print(ethereum_cleaned_df.isnull().sum())
print(ethereum_cleaned_df.duplicated().any())

print(xrp_cleaned_df.isnull().sum())
print(xrp_cleaned_df.duplicated().any())

print(dogecoin_cleaned_df.isnull().sum())
print(dogecoin_cleaned_df.duplicated().any())

print(solana_cleaned_df.isnull().sum())
print(solana_cleaned_df.duplicated().any())

Date      0
Open      0
High      0
Low       0
Close     0
Volume    0
dtype: int64
False
Date      0
Open      0
High      0
Low       0
Close     0
Volume    0
dtype: int64
False
Date      0
Open      0
High      0
Low       0
Close     0
Volume    0
dtype: int64
False
Date      0
Open      0
High      0
Low       0
Close     0
Volume    0
dtype: int64
False
Date      0
Open      0
High      0
Low       0
Close     0
Volume    0
dtype: int64
False


**4. Convert date from object to datetime datatype and share price and GDP information from object to float datatype.**

In [ ]:
bitcoin_cleaned_df['Date'] = pd.to_datetime(bitcoin_cleaned_df['Date'])
ethereum_cleaned_df['Date'] = pd.to_datetime(ethereum_cleaned_df['Date'])
xrp_cleaned_df['Date'] = pd.to_datetime(xrp_cleaned_df['Date'])
dogecoin_cleaned_df['Date'] = pd.to_datetime(dogecoin_cleaned_df['Date'])
solana_cleaned_df['Date'] = pd.to_datetime(solana_cleaned_df['Date'])

bitcoin_cleaned_df[['Open', 'High', 'Low', 'Close', 'Volume']] = bitcoin_cleaned_df[['Open', 'High', 'Low', 'Close', 'Volume']].astype(float).round(2)
ethereum_cleaned_df[['Open', 'High', 'Low', 'Close', 'Volume']] = ethereum_cleaned_df[['Open', 'High', 'Low', 'Close', 'Volume']].astype(float).round(2)
xrp_cleaned_df[['Open', 'High', 'Low', 'Close', 'Volume']] = xrp_cleaned_df[['Open', 'High', 'Low', 'Close', 'Volume']].astype(float).round(2)
dogecoin_cleaned_df[['Open', 'High', 'Low', 'Close', 'Volume']] = dogecoin_cleaned_df[['Open', 'High', 'Low', 'Close', 'Volume']].astype(float).round(2)
solana_cleaned_df[['Open', 'High', 'Low', 'Close', 'Volume']] = solana_cleaned_df[['Open', 'High', 'Low', 'Close', 'Volume']].astype(float).round(2)

print(bitcoin_cleaned_df.info())
print(ethereum_cleaned_df.info())
print(xrp_cleaned_df.info())
print(dogecoin_cleaned_df.info())
print(solana_cleaned_df.info())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 350 entries, 0 to 349
Data columns (total 6 columns):
 #   Column  Non-Null Count  Dtype         
---  ------  --------------  -----         
 0   Date    350 non-null    datetime64[ns]
 1   Open    350 non-null    float64       
 2   High    350 non-null    float64       
 3   Low     350 non-null    float64       
 4   Close   350 non-null    float64       
 5   Volume  350 non-null    float64       
dtypes: datetime64[ns](1), float64(5)
memory usage: 16.5 KB
None
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 350 entries, 0 to 349
Data columns (total 6 columns):
 #   Column  Non-Null Count  Dtype         
---  ------  --------------  -----         
 0   Date    350 non-null    datetime64[ns]
 1   Open    350 non-null    float64       
 2   High    350 non-null    float64       
 3   Low     350 non-null    float64       
 4   Close   350 non-null    float64       
 5   Volume  350 non-null    float64       
dtypes: datetime64[ns](

**5. Calculate new columns for daily return, 5-day moving average, and 5-day rolling volatility.**

In [ ]:
bitcoin_cleaned_df['Daily Return (%)'] = (bitcoin_cleaned_df['Close'].pct_change() * 100).round(2)
bitcoin_cleaned_df['5-Day Moving Average'] = bitcoin_cleaned_df['Close'].rolling(window = 5).mean().round(2)
bitcoin_cleaned_df['5-Day Rolling Volatility'] = bitcoin_cleaned_df['Daily Return (%)'].rolling(window = 5).std().round(2)

ethereum_cleaned_df['Daily Return (%)'] = (ethereum_cleaned_df['Close'].pct_change() * 100).round(2)
ethereum_cleaned_df['5-Day Moving Average'] = ethereum_cleaned_df['Close'].rolling(window = 5).mean().round(2)
ethereum_cleaned_df['5-Day Rolling Volatility'] = ethereum_cleaned_df['Daily Return (%)'].rolling(window = 5).std().round(2)

xrp_cleaned_df['Daily Return (%)'] = (xrp_cleaned_df['Close'].pct_change() * 100).round(2)
xrp_cleaned_df['5-Day Moving Average'] = xrp_cleaned_df['Close'].rolling(window = 5).mean().round(2)
xrp_cleaned_df['5-Day Rolling Volatility'] = xrp_cleaned_df['Daily Return (%)'].rolling(window = 5).std().round(2)

dogecoin_cleaned_df['Daily Return (%)'] = (dogecoin_cleaned_df['Close'].pct_change() * 100).round(2)
dogecoin_cleaned_df['5-Day Moving Average'] = dogecoin_cleaned_df['Close'].rolling(window = 5).mean().round(2)
dogecoin_cleaned_df['5-Day Rolling Volatility'] = dogecoin_cleaned_df['Daily Return (%)'].rolling(window = 5).std().round(2)

solana_cleaned_df['Daily Return (%)'] = (solana_cleaned_df['Close'].pct_change() * 100).round(2)
solana_cleaned_df['5-Day Moving Average'] = solana_cleaned_df['Close'].rolling(window = 5).mean().round(2)
solana_cleaned_df['5-Day Rolling Volatility'] = solana_cleaned_df['Daily Return (%)'].rolling(window = 5).std().round(2)

In [16]:
# After cleaning and adding new columns, export cleaned data as new csv files
bitcoin_cleaned_df.to_csv('./Datasets/Bitcoin_cleaned_daily data.csv', index = False)
ethereum_cleaned_df.to_csv('./Datasets/Ethereum_cleaned_daily data.csv', index = False)
xrp_cleaned_df.to_csv('./Datasets/XRP_cleaned_daily data.csv', index = False)
dogecoin_cleaned_df.to_csv('./Datasets/Dogecoin_cleaned_daily data.csv', index = False)
solana_cleaned_df.to_csv('./Datasets/Solana_cleaned_daily data.csv', index = False)

**6. Create plots of the various cryptocurrencies for exploratory data analysis.**

In [17]:
# Create a subplot of all 5 cryptocurrencies using candlestick plots from Jul 2024 to Jul 2025
fig3 = make_subplots(rows = 5, cols = 1, shared_xaxes = True, subplot_titles=('Bitcoin', 'Ethereum', 'XRP', 'Dogecoin', 'Solana'), vertical_spacing = 0.05, y_title = "USD")

fig3.add_trace(go.Candlestick(x = bitcoin_cleaned_df['Date'], open = bitcoin_cleaned_df['Open'], high = bitcoin_cleaned_df['High'], low = bitcoin_cleaned_df['Low'], close = bitcoin_cleaned_df['Close'], 
                              name = 'BTC', showlegend = False), row = 1, col = 1)
fig3.add_trace(go.Scatter(x = bitcoin_cleaned_df['Date'], y = bitcoin_cleaned_df['5-Day Moving Average'], line = dict(color = 'black', width=1), name = "5-Day Moving Average", showlegend = False), 
                          row = 1, col = 1)

fig3.add_trace(go.Candlestick(x = ethereum_cleaned_df['Date'], open = ethereum_cleaned_df['Open'], high = ethereum_cleaned_df['High'], low = ethereum_cleaned_df['Low'], 
                              close = ethereum_cleaned_df['Close'], name = 'ETH', showlegend = False), row = 2, col = 1)
fig3.add_trace(go.Scatter(x = ethereum_cleaned_df['Date'], y = ethereum_cleaned_df['5-Day Moving Average'], line = dict(color = 'black', width=1), name = "5-Day Moving Average", showlegend = False), 
               row = 2, col = 1)

fig3.add_trace(go.Candlestick(x = xrp_cleaned_df['Date'], open = xrp_cleaned_df['Open'], high = xrp_cleaned_df['High'], low = xrp_cleaned_df['Low'], close = xrp_cleaned_df['Close'], 
                              name = 'Candlesticks', showlegend = True), row = 3, col = 1)
fig3.add_trace(go.Scatter(x = xrp_cleaned_df['Date'], y = xrp_cleaned_df['5-Day Moving Average'], line = dict(color = 'black', width=1), name = "5-Day Moving Average", showlegend = True), 
               row = 3, col = 1)

fig3.add_trace(go.Candlestick(x = dogecoin_cleaned_df['Date'], open = dogecoin_cleaned_df['Open'], high = dogecoin_cleaned_df['High'], low = dogecoin_cleaned_df['Low'], 
                              close = dogecoin_cleaned_df['Close'], name = 'DOGE', showlegend = False), row = 4, col = 1)
fig3.add_trace(go.Scatter(x = dogecoin_cleaned_df['Date'], y = dogecoin_cleaned_df['5-Day Moving Average'], line = dict(color = 'black', width=1), name = "5-Day Moving Average", showlegend = False), 
               row = 4, col = 1)

fig3.add_trace(go.Candlestick(x = solana_cleaned_df['Date'], open = solana_cleaned_df['Open'], high = solana_cleaned_df['High'], low = solana_cleaned_df['Low'], close = solana_cleaned_df['Close'], 
                              name = 'SOL', showlegend = False), row = 5, col = 1)
fig3.add_trace(go.Scatter(x = solana_cleaned_df['Date'], y = solana_cleaned_df['5-Day Moving Average'], line = dict(color = 'black', width=1), name = "5-Day Moving Average", showlegend = False), 
               row = 5, col = 1)

fig3.update_layout(title = {'x' : 0.5, 'y' : 1, 'xanchor' : 'center'}, margin = dict(l = 65, r = 40, t = 40, b = 30), hovermode="x", width = 750, height = 750,
                  legend=dict(x = 0.05, y = 0.55, xanchor = 'left', yanchor = 'top', bgcolor = 'rgba(255, 255, 255, 0.5)'))

fig3.update_xaxes(range=['2024-07-18', '2025-07-02'], row = 1, col = 1)
fig3.update_xaxes(range=['2024-07-18', '2025-07-02'], row = 2, col = 1)
fig3.update_xaxes(range=['2024-07-18', '2025-07-02'], row = 3, col = 1)
fig3.update_xaxes(range=['2024-07-18', '2025-07-02'], row = 4, col = 1)
fig3.update_xaxes(range=['2024-07-18', '2025-07-02'], row = 5, col = 1)
fig3.update_xaxes(rangeslider_visible=False)

fig3.show()

In [18]:
# Create a subplot of Bitcoin, VXX, and VTI candlestick plots from Jul 2024 to Jul 2025
fig4 = make_subplots(rows = 3, cols = 1, shared_xaxes = True, subplot_titles=('Bitcoin', 'VTI ETF', 'VXX ETN'), vertical_spacing = 0.05, y_title = "USD")

fig4.add_trace(go.Candlestick(x = bitcoin_cleaned_df['Date'], open = bitcoin_cleaned_df['Open'], high = bitcoin_cleaned_df['High'], low = bitcoin_cleaned_df['Low'], close = bitcoin_cleaned_df['Close'], 
                              name = 'BTC', showlegend = False), row = 1, col = 1)
fig4.add_trace(go.Scatter(x = bitcoin_cleaned_df['Date'], y = bitcoin_cleaned_df['5-Day Moving Average'], line = dict(color = 'black', width=1), name = '5-Day Moving Average', showlegend = False), 
                          row = 1, col = 1)

fig4.add_trace(go.Candlestick(x = VTI_cleaned_df['Date'], open = VTI_cleaned_df['Open'], high = VTI_cleaned_df['High'], low = VTI_cleaned_df['Low'], close = VTI_cleaned_df['Close'], 
                              name = 'Candlesticks', showlegend = True), row = 2, col = 1)
fig4.add_trace(go.Scatter(x = VTI_cleaned_df['Date'], y = VTI_cleaned_df['5-Day Moving Average'], line = dict(color = 'black', width=1), name = '5-Day Moving Average', showlegend = True), 
                          row = 2, col = 1)

fig4.add_trace(go.Candlestick(x = VXX_cleaned_df['Date'], open = VXX_cleaned_df['Open'], high = VXX_cleaned_df['High'], low = VXX_cleaned_df['Low'], close = VXX_cleaned_df['Close'], 
                              name = 'VXX', showlegend = False), row = 3, col = 1)
fig4.add_trace(go.Scatter(x = VXX_cleaned_df['Date'], y = VXX_cleaned_df['5-Day Moving Average'], line = dict(color = 'black', width=1), name = '5-Day Moving Average', showlegend = False), 
                          row = 3, col = 1)

fig4.update_layout(title = {'x' : 0.5, 'y' : 1, 'xanchor' : 'center'}, margin = dict(l = 65, r = 40, t = 40, b = 30), hovermode="x", width = 750, height = 750, 
                  legend=dict(x = 0.25, y = 0.48, xanchor = 'left', yanchor = 'top', bgcolor = 'rgba(255, 255, 255, 0.5)'))

fig4.update_yaxes(range=[230, 310], row = 2, col = 1)
fig4.update_yaxes(range=[10, 100], row = 3, col = 1)

fig4.update_xaxes(range=['2024-07-18', '2025-07-02'], row = 1, col = 1)
fig4.update_xaxes(range=['2024-07-18', '2025-07-02'], row = 2, col = 1)
fig4.update_xaxes(range=['2024-07-18', '2025-07-02'], row = 3, col = 1)
fig4.update_xaxes(rangeslider_visible=False)

fig4.show()

Export plots as png files.

In [ ]:
# fig.write_image('Comparison of GDP to VTI ETF and VXX ETN from 2024 to 2025.png', width = 750, height = 750, scale = 3)
# fig2.write_image('Comparison of GDP to VTI ETF and VXX ETN from 2015 to 2025.png', width = 750, height = 750, scale = 3)
# fig3.write_image('Comparison of Bitcoin, Ethereum, XRP, Dogecoin, and Solana.png', width = 750, height = 750, scale = 3)
# fig4.write_image('Comparison of Bitcoin to VTI ETF and VXX ETN.png', width = 750, height = 750, scale = 3)